# Pull Form 13s


In [15]:
%%capture
%pip install pandas requests-ratelimiter xmltodict

## Download Raw Form 13 Files

In [16]:
import io
import math
from typing import Tuple
import datetime
import os
import csv
import xmltodict

from requests_ratelimiter import LimiterSession

session = LimiterSession(per_second=10)

def pull_form13s(output_dir:str='data/form13',
         dates_from_to:Tuple[str,str] = ('2023-01-01', '2024-01-01'),
         user_email:str='sales@neo4j.com',
         user_name='Neo4j') -> int:

    start_date = datetime.datetime.strptime( dates_from_to[0], '%Y-%m-%d').date()
    date = datetime.datetime.strptime( dates_from_to[1], '%Y-%m-%d').date()
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    while date >= start_date:
        print(date)
        download_date(date, output_dir, f'{user_name} {user_email}')
        date = date - datetime.timedelta(days=1)
    return 0

def download_date(date, output_dir, user_agent):
    form13_paths = get_form13_urls(date)
    # Download each Form 13
    print('We have ' + str(len(form13_paths)) + ' Form 13 URLs for the date ' + str(date))
    for path in form13_paths:
        try:
            filings = download_form13(path, user_agent)
            with open(os.path.join(output_dir, path.replace('/', '_')), 'w') as file:
                file.write(filings)
        except Exception as e:
            print(e)


def get_form13_urls(date):
    print('Composing the URL of the master file...')
    year = str(date.year)
    quarter = 'QTR' + str(math.ceil(date.month / 3))
    date = date.strftime('%Y%m%d')
    path = '/Archives/edgar/daily-index/' + year + '/' + quarter + '/master.' + date + '.idx'
    url = 'https://www.sec.gov' + path
    print('The URL of the master file is ' + url)

    print('Downloading the master file...')
    # conn = http.client.HTTPSConnection('www.sec.gov')
    # conn.request('GET', path, headers={'User-Agent': 'Neo4j Ben.Lackey@Neo4j.com'})
    # response = conn.getresponse()
    #data = response.read()
    # conn.close()
    response = session.get('https://www.sec.gov/' + path, headers={'User-Agent': 'Neo4j andreas.kollegger@neo4j.com'})
    print(response.status_code)

    if response.status_code == 200: # and response.reason == 'OK':
        # text = data.decode('windows-1252')
        text = response.text
        form4_paths = parse_master_file(text)
        return form4_paths
    else:
        print('Download failed for master file.', response.status_code)
        return []


def parse_master_file(text):
    print('Parsing the master file...')
    form4_paths = []
    file = io.StringIO(text)
    reader = csv.reader(file, delimiter='|')
    for row in reader:
        if len(row) != 5:
            # This is a header
            pass
        elif row[2] == '13F-HR':
            # This is a Form 13
            form4_paths.append('/Archives/' + row[4])

    return form4_paths


def download_form13(path, user_agent):
    # conn = http.client.HTTPSConnection('www.sec.gov')
    # conn.request('GET', path, headers={'User-Agent': 'Neo4j sales@neo4j.com'})
    # response = conn.getresponse()
    # data = response.read()
    # conn.close()
    response = session.get('https://www.sec.gov/' + path, headers={'User-Agent': user_agent})

    if response.status_code == 200: # and response.reason == 'OK':
        print('http://sec.gov' + path)
        # text = data.decode('utf-8')
        text = response.text
        file = io.StringIO(text)
        contents = file.read()
        file.close()
        return contents
    else:
        print('Download failed for form13 file: HTTP ', response.status_code)
        return []


In [18]:
pull_form13s(dates_from_to=('2023-01-01', '2024-01-01'))

2024-01-01
Composing the URL of the master file...
The URL of the master file is https://www.sec.gov/Archives/edgar/daily-index/2024/QTR1/master.20240101.idx
403
Download failed for master file. 403
We have 0 Form 13 URLs for the date 2024-01-01
2023-12-31
Composing the URL of the master file...
The URL of the master file is https://www.sec.gov/Archives/edgar/daily-index/2023/QTR4/master.20231231.idx
403
Download failed for master file. 403
We have 0 Form 13 URLs for the date 2023-12-31
2023-12-30
Composing the URL of the master file...
The URL of the master file is https://www.sec.gov/Archives/edgar/daily-index/2023/QTR4/master.20231230.idx
403
Download failed for master file. 403
We have 0 Form 13 URLs for the date 2023-12-30
2023-12-29
Composing the URL of the master file...
The URL of the master file is https://www.sec.gov/Archives/edgar/daily-index/2023/QTR4/master.20231229.idx
200
Parsing the master file...
We have 0 Form 13 URLs for the date 2023-12-29
2023-12-28
Composing the U

0

## Format Form13 Info to CSV and Save

In [19]:
from typing import List, Dict
import pandas as pd
import xmltodict

FILING_MANAGER_NAME_COL = 'managerName'
FILING_MANAGER_CIK_COL = 'managerCik'
REPORT_PERIOD_COL = 'reportCalendarOrQuarter'
COMPANY_CUSIP_COL = 'cusip'
COMPANY_CUSIP6_COL = 'cusip6'
COMPANY_NAME_COL = 'companyName'
SOURCE_ID_COL = 'source'
VALUE_COL = 'value'
SHARES_COL = 'shares'


def format_form13s(input_dir:str='data/form13',
                   user_email:str='sales@neo4j.com',
                   user_name='Neo4j', top_periods:int=4) -> pd.DataFrame:
    filings_df, failures = parse_from_dir(input_dir)
    stg_df = aggregate_data(filings_df)
    if top_periods is not None:
        stg_df = filter_data(stg_df, top_periods)
    print(f'===== Had {len(failures)} failed file parsings ====')
    for failure in failures:
        print(failure)
    return stg_df


# function to strip namespaces post xmltodict transformation
def strip_ns(x):
    if isinstance(x, dict):
        x_striped = dict()
        for k, v in x.items():
            x_striped[k.split(':')[-1]] = strip_ns(v)
    elif isinstance(x, list):
        x_striped = [strip_ns(i) for i in x]
    else:
        x_striped = x
    return x_striped


def extract_submission_info(contents: str) -> str:
    xml = contents[1].split('</XML>')[0].strip()
    return strip_ns(xmltodict.parse(xml))['edgarSubmission']


def extract_investment_info(contents: str) -> str:
    xml = contents[2].split('</XML>')[0].strip()
    return strip_ns(xmltodict.parse(xml))['informationTable']['infoTable']


def estimate_cusip6(cusip: str) -> str:
    # Padding of 3 zeros is suspect - likely has a padded zero. This is inconsistent among form13 filers
    if cusip.startswith('000'):
        return cusip.upper()[1:7]
    return cusip.upper()[:6]


def filter_and_format(info_tables: str, manager_cik: str, manager_name: str,
                      report_period: datetime.date) -> List[Dict]:
    res = []
    if isinstance(info_tables, dict):
        info_tables = [info_tables]
    for info_table in info_tables:
        # Skip none to report incidences
        if info_table['cusip'] == '000000000':
            pass
        # Only want stock holdings, not options
        if info_table['shrsOrPrnAmt']['sshPrnamtType'] != 'SH':
            pass
        # Only want holdings over $10m
        elif (float(info_table['value']) * 1000) < 10000000:
            pass
        # Only want common stock
        elif info_table['titleOfClass'] != 'COM':
            pass
        else:
            res.append({FILING_MANAGER_CIK_COL: manager_cik,
                        FILING_MANAGER_NAME_COL: manager_name,
                        REPORT_PERIOD_COL: report_period,
                        COMPANY_CUSIP_COL: info_table['cusip'].upper(),
                        COMPANY_CUSIP6_COL: estimate_cusip6(info_table['cusip']),
                        COMPANY_NAME_COL: info_table['nameOfIssuer'],
                        VALUE_COL: info_table['value'].replace(' ', '') + '000',
                        SHARES_COL: info_table['shrsOrPrnAmt']['sshPrnamt']})
    return res


def extract_dicts(txt: str) -> List[Dict]:
    contents = txt.split('<XML>')
    submt_dict = extract_submission_info(contents)
    mng_cik = submt_dict['headerData']['filerInfo']['filer']['credentials']['cik']
    mng_name = submt_dict['formData']['coverPage']['filingManager']['name']
    report_period = submt_dict['formData']['coverPage']['reportCalendarOrQuarter']
    info_dict = extract_investment_info(contents)
    return filter_and_format(info_dict, mng_cik, mng_name, report_period)


def parse_from_dir(directory_path: str):
    # Go through all files and concatenate to dataframe
    print(f'=== Begin Parsing from {directory_path} ===')
    filing_dfs = []
    failures = []
    for file_name in os.listdir(directory_path):
        if file_name.endswith('.txt'):
            print(f'parsing {file_name}')
            file_path = os.path.join(directory_path, file_name)
            try:
                with open(file_path, 'r') as file:
                    filing = extract_dicts(file.read())
                    tmp_filing_df = pd.DataFrame(filing)
                    tmp_filing_df[SOURCE_ID_COL] = 'https://sec.gov' + file_name.replace('_', '/')
                    filing_dfs.append(tmp_filing_df)
            except Exception as e:
                print(e)
                failures.append(file_name)
    filing_df = pd.concat(filing_dfs, ignore_index=True)
    filing_df[REPORT_PERIOD_COL] = pd.to_datetime(filing_df[REPORT_PERIOD_COL]).dt.date
    filing_df[VALUE_COL] = filing_df[VALUE_COL].astype(float)
    filing_df[SHARES_COL] = filing_df[SHARES_COL].astype(int)
    return filing_df, failures


# This data contains duplicates where an asset is reported more than once for the same filing manager within the same
# report calendar/quarter.
# See for example https://www.sec.gov/Archives/edgar/data/1962636/000139834423009400/0001398344-23-009400.txt
# for our intents and purposes we will sum over values and shares to aggregate the duplicates out
def aggregate_data(filings_df: pd.DataFrame) -> pd.DataFrame:
    print(f'=== Aggregating Parsed Data ===')
    return filings_df.groupby([SOURCE_ID_COL, FILING_MANAGER_CIK_COL, FILING_MANAGER_NAME_COL, REPORT_PERIOD_COL,
                               COMPANY_CUSIP6_COL, COMPANY_CUSIP_COL]) \
        .agg({COMPANY_NAME_COL: 'first', VALUE_COL: "sum", SHARES_COL: "sum"}).reset_index()


def filter_data(filings_df: pd.DataFrame, top_n_periods: int) -> pd.DataFrame:
    print(f'=== Filtering Data ===')
    periods_df = filings_df[[REPORT_PERIOD_COL, VALUE_COL]] \
        .groupby(REPORT_PERIOD_COL).count().reset_index().sort_values(REPORT_PERIOD_COL)
    num_periods = min(periods_df.shape[0], top_n_periods)
    top_periods = periods_df[REPORT_PERIOD_COL][-num_periods:].tolist()
    return filings_df[filings_df[REPORT_PERIOD_COL].isin(top_periods)]

In [20]:
form13_df = format_form13s()
form13_df

=== Begin Parsing from data/form13 ===
parsing _Archives_edgar_data_805676_0001104659-23-011190.txt
parsing _Archives_edgar_data_1214822_0001214822-23-000006.txt
parsing _Archives_edgar_data_1956031_0001104659-23-117629.txt
parsing _Archives_edgar_data_1681662_0001681662-23-000004.txt
parsing _Archives_edgar_data_1771377_0001013594-23-000915.txt
parsing _Archives_edgar_data_1822065_0001085146-23-001659.txt
parsing _Archives_edgar_data_1780365_0001085146-23-002856.txt
parsing _Archives_edgar_data_1659718_0001659718-23-000002.txt
parsing _Archives_edgar_data_1730386_0000950123-23-003832.txt
parsing _Archives_edgar_data_1698093_0001698093-23-000001.txt
parsing _Archives_edgar_data_1725357_0001085146-23-001588.txt
parsing _Archives_edgar_data_1352342_0000919574-23-006238.txt
parsing _Archives_edgar_data_1680964_0001172661-23-002194.txt
parsing _Archives_edgar_data_1529872_0001085146-23-002350.txt
parsing _Archives_edgar_data_1383782_0001172661-23-000276.txt
parsing _Archives_edgar_data_179

source  managerCik  \
0        https://sec.gov/Archives/edgar/data/1000097/00...  0001000097   
1        https://sec.gov/Archives/edgar/data/1000097/00...  0001000097   
2        https://sec.gov/Archives/edgar/data/1000097/00...  0001000097   
3        https://sec.gov/Archives/edgar/data/1000097/00...  0001000097   
4        https://sec.gov/Archives/edgar/data/1000097/00...  0001000097   
...                                                    ...         ...   
2694585  https://sec.gov/Archives/edgar/data/98758/0000...  0000098758   
2694586  https://sec.gov/Archives/edgar/data/98758/0000...  0000098758   
2694587  https://sec.gov/Archives/edgar/data/98758/0000...  0000098758   
2694588  https://sec.gov/Archives/edgar/data/98758/0000...  0000098758   
2694589  https://sec.gov/Archives/edgar/data/98758/0000...  0000098758   

                                managerName reportCalendarOrQuarter  cusip6  \
0        KINGDON CAPITAL MANAGEMENT, L.L.C.              2022-12-31  03769M   
1        KINGDON CAPITAL MANAGEMENT, L.L.C.              2022-12-31  03852U   
2        KINGDON CAPITAL MANAGEMENT, L.L.C.              2022-12-31  05605H   
3        KINGDON CAPITAL MANAGEMENT, L.L.C.              2022-12-31  060505   
4        KINGDON CAPITAL MANAGEMENT, L.L.C.              2022-12-31  075887   
...                                     ...                     ...     ...   
2694585      Torray Investment Partners LLC              2023-09-30  G29183   
2694586      Torray Investment Partners LLC              2023-09-30  G7709Q   
2694587      Torray Investment Partners LLC              2023-09-30  G7T16G   
2694588      Torray Investment Partners LLC              2023-09-30  H1467J   
2694589      Torray Investment Partners LLC              2023-09-30  N53745   

             cusip                companyName         value  shares  
0        03769M106     APOLLO GLOBAL MGMT INC  9.568500e+09  150000  
1        03852U106                    ARAMARK  1.240200e+10  300000  
2        05605H100       BWX TECHNOLOGIES INC  1.951488e+10  336000  
3        060505104          BANK AMERICA CORP  1.324800e+10  400000  
4        075887109      BECTON DICKINSON & CO  2.265813e+10   89100  
...            ...                        ...           ...     ...  
2694585  G29183103                      Eaton  1.492448e+10   69976  
2694586  G7709Q104         Royalty Pharma Plc  1.119886e+10  412633  
2694587  G7T16G103                    Sapiens  1.227408e+09   43173  
2694588  H1467J104              Chubb Limited  1.110786e+10   53357  
2694589  N53745100  LyondellBasell Industries  3.130835e+09   33061  

[2651322 rows x 9 columns]

In [21]:
form13_df.to_csv('data/form13.csv', index=False)